In [2]:
!pip install transformers datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 472.7/472.7 kB 17.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 15.0 MB/s eta 0:00:00


In [4]:
import json
import pandas as pd

# Load Spider dataset
def load_spider_data(path):
    with open(path, 'r') as f:
        data = json.load(f)

    questions = []
    queries = []

    for entry in data:
        questions.append(entry['question'])
        queries.append(entry['query'])

    return pd.DataFrame({'question': questions, 'query': queries})

# Load the uploaded file
train_data = load_spider_data('/content/train_spider.json')
train_data.head()

question  \
0  How many heads of the departments are older th...   
1  List the name, born state and age of the heads...   
2  List the creation year, name and budget of eac...   
3  What are the maximum and minimum budget of the...   
4  What is the average number of employees of the...   

                                               query  
0         SELECT count(*) FROM head WHERE age  >  56  
1  SELECT name ,  born_state ,  age FROM head ORD...  
2  SELECT creation ,  name ,  budget_in_billions ...  
3  SELECT max(budget_in_billions) ,  min(budget_i...  
4  SELECT avg(num_employees) FROM department WHER...

In [5]:
from transformers import T5Tokenizer, T5ForConditionalGeneration

model_name = "t5-small"  # Use "t5-base" or "t5-large" for better results
tokenizer = T5Tokenizer.from_pretrained(model_name)
model = T5ForConditionalGeneration.from_pretrained(model_name)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/2.32k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.39M [00:00<?, ?B/s]

You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565


config.json:   0%|          | 0.00/1.21k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/242M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/147 [00:00<?, ?B/s]

In [6]:
# Tokenize data
def preprocess_data(examples):
    inputs = ["translate English to SQL: " + q for q in examples['question']]
    targets = [sql for sql in examples['query']]
    model_inputs = tokenizer(inputs, max_length=128, truncation=True, padding="max_length")
    print(model_inputs)
    labels = tokenizer(targets, max_length=128, truncation=True, padding="max_length").input_ids
    model_inputs["labels"] = labels
    return model_inputs

In [7]:
# Process the dataset for training
from datasets import Dataset
train_dataset = Dataset.from_pandas(train_data)
print(train_dataset)
train_dataset = train_dataset.map(preprocess_data, batched=True)
print(train_dataset)
train_dataset.set_format(type="torch", columns=["input_ids", "attention_mask", "labels"])
print(train_dataset)

Dataset({
    features: ['question', 'query'],
    num_rows: 7000
})


Map:   0%|          | 0/7000 [00:00<?, ? examples/s]

{'input_ids': [[13959, 1566, 12, 12558, 10, 571, 186, 7701, 13, 8, 10521, 33, 2749, 145, 11526, 3, 58, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [13959, 1566, 12, 12558, 10, 6792, 8, 564, 6, 2170, 538, 11, 1246, 13, 8, 7701, 13, 10521, 5563, 57, 1246, 5, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], [13959, 1566, 12, 12558, 10, 6792, 8, 3409, 215, 6, 564, 11, 1487, 13, 284, 3066, 5, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

In [9]:
from transformers import Trainer, TrainingArguments

training_args = TrainingArguments(
    output_dir="./results",
    evaluation_strategy="no",
    learning_rate=5e-5,
    per_device_train_batch_size=8,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
)

# Train the model
trainer.train()

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


TrainOutput(global_step=2625, training_loss=0.3563073570614769, metrics={'train_runtime': 461.0212, 'train_samples_per_second': 45.551, 'train_steps_per_second': 5.694, 'total_flos': 710544457728000.0, 'train_loss': 0.3563073570614769, 'epoch': 3.0})

In [13]:
# Define a function to generate SQL queries
def generate_sql(question):
    input_text = "translate English to SQL: " + question
    input_ids = tokenizer.encode(input_text, return_tensors="pt").to(model.device) # Move input_ids to the same device as the model
    output = model.generate(input_ids, max_length=128)
    sql_query = tokenizer.decode(output[0], skip_special_tokens=True)
    return sql_query

# Test with a sample question
question = "What are the names of the stadiums without any concerts ? ||| concert_singer"
print("Question:", question)
print("Generated SQL Query:", generate_sql(question))

Question: What are the names of the stadiums without any concerts ? ||| concert_singer
Generated SQL Query: SELECT T1.singer_name FROM stadiums AS T1 JOIN concerts AS T2 ON T1.singer_id = T2.singer_id
